In [2]:
from deeppavlov import build_model, configs
from tqdm import tqdm_notebook as tqdm
import json
from os import listdir
from os.path import join
from nltk.tokenize import WordPunctTokenizer
import numpy as np
from sklearn.model_selection import train_test_split
from queue import Queue
from collections import defaultdict, Counter

### Лемматизация от deeppavlov

Эта лемматизация слишком простая. Хотим более сложную, где будет морфотеггинг, а также начальная форма

In [4]:
model = build_model(configs.morpho_tagger.BERT.morpho_ru_syntagrus_bert, download=False)

2020-03-23 01:27:27.652 INFO in 'deeppavlov.core.data.simple_vocab'['simple_vocab'] at line 115: [loading vocabulary from /home/loginov-ra/.deeppavlov/models/morpho_ru_syntagrus/tag.dict]
2020-03-23 01:27:50.258 INFO in 'deeppavlov.core.models.tf_model'['tf_model'] at line 51: [loading model from /home/loginov-ra/.deeppavlov/models/morpho_ru_syntagrus/model]


INFO:tensorflow:Restoring parameters from /home/loginov-ra/.deeppavlov/models/morpho_ru_syntagrus/model


2020-03-23 01:27:51.697 WARNING in 'deeppavlov.core.models.serializable'['serializable'] at line 52: No load path is set for UDPymorphyLemmatizer!


In [3]:
sentence = "Кони неслись по гулкой мостовой, сметая всё на своём пути"

In [4]:
sentences = ["Кони неслись по гулкой мостовой, сметая всё на своём пути.", "Девушка пела в церковном хоре о всех уставших в чужом краю."]
for parse in model(sentences):
    print(parse)

1	Кони	конь	NOUN	_	Animacy=Anim|Case=Nom|Gender=Masc|Number=Plur	_	_	_	_
2	неслись	нестись	VERB	_	Aspect=Imp|Mood=Ind|Number=Plur|Tense=Past|VerbForm=Fin|Voice=Mid	_	_	_	_
3	по	по	ADP	_	_	_	_	_	_
4	гулкой	гулкий	ADJ	_	Case=Dat|Degree=Pos|Gender=Fem|Number=Sing	_	_	_	_
5	мостовой	мостовая	NOUN	_	Animacy=Inan|Case=Dat|Gender=Fem|Number=Sing	_	_	_	_
6	,	,	PUNCT	_	_	_	_	_	_
7	сметая	сметать	VERB	_	Aspect=Imp|Tense=Pres|VerbForm=Conv|Voice=Act	_	_	_	_
8	всё	весь	PRON	_	Animacy=Inan|Case=Acc|Gender=Neut|Number=Sing	_	_	_	_
9	на	на	ADP	_	_	_	_	_	_
10	своём	свой	DET	_	Case=Loc|Gender=Masc|Number=Sing	_	_	_	_
11	пути	путь	NOUN	_	Animacy=Inan|Case=Loc|Gender=Masc|Number=Sing	_	_	_	_
12	.	.	PUNCT	_	_	_	_	_	_

1	Девушка	девушка	NOUN	_	Animacy=Anim|Case=Nom|Gender=Fem|Number=Sing	_	_	_	_
2	пела	петь	VERB	_	Aspect=Imp|Gender=Fem|Mood=Ind|Number=Sing|Tense=Past|VerbForm=Fin|Voice=Act	_	_	_	_
3	в	в	ADP	_	_	_	_	_	_
4	церковном	церковный	ADJ	_	Case=Loc|Degree=Pos|Gender=Masc|Number=Sing	_	_	_	_
5	хоре	х

In [5]:
sentences = ["Кони неслись по гулкой мостовой, сметая всё на своём пути."]
print(model(sentences)[0].split('\n')[2].split('\t')[2])

по


In [6]:
def lemmatize_sentence_short(sentence):
    sentences = [sentence]
    morpho_tokens = model(sentences)[0].split('\n')
    lemmatized_tokens = [x.split('\t')[2] for x in morpho_tokens if len(x.split('\t')) == 10]
    return ' '.join(list(lemmatized_tokens))

def lemmatize_sentence(sentence):
    ans_parts = []
    tokens = WordPunctTokenizer().tokenize(sentence)
    n_tokens = len(tokens)
    
    if n_tokens < 256:
        return lemmatize_sentence_short(sentence)
    else:
        return ""
    
    i = 0
    
    while i < n_tokens:
        if i + 256 < n_tokens:
            finish_i = i + 256
        else:
            finish_i = n_tokens
        
        ans_parts.append(lemmatize_sentence_short(' '.join(tokens[i:finish_i])))
        i += 256
        
    return ' '.join(ans_parts)

In [7]:
lemmatize_sentence(sentences[0])

'конь нестись по гулкий мостовая , сметать весь на свой путь .'

### Тезаурус Лукашевич

Разберемся с тем, как можно парсить тезаурус. Для начала соберём словарь понятий из html, затем из файла прочитаем отношения ВЫШЕ-НИЖЕ, полезные для поиска гиперонимов

In [9]:
def preprocess_token(name):
    if '(' in name:
        name = name.split('(')[0][:-1]
    return lemmatize_sentence(name)

def preprocess_multiterm(term):
    return [preprocess_token(token.strip()) for token in term.split(',')]

In [10]:
from lxml import etree
from io import StringIO, BytesIO
from collections import defaultdict
import sys

In [11]:
def get_id_to_word_matching(concepts_filename):
    id_to_words = dict()
    words_to_id = dict()
    
    with open(concepts_filename) as xml_file:
        xml = xml_file.read()
    
    root = etree.fromstring(xml)
    
    for concept in tqdm(root.getchildren()):
        name = concept.find('name')
        idx = concept.get('id')
        terms = preprocess_multiterm(name.text)
        
        for term in terms:
            words_to_id[term] = int(idx)
            id_to_words[int(idx)] = term
                
    return id_to_words, words_to_id

In [12]:
id_to_words, words_to_id = get_id_to_word_matching('RuThes/concepts.xml')

KeyboardInterrupt: 

In [76]:
words_to_id['российский федерация']

2636

In [80]:
words_to_id['абажур']

110725

In [81]:
words_to_id['плафон']

110725

Получили соответствие номеров сущностей и самих слов и наоборот. К сожалению, нескольким словам может соответствовать один и тот же номер сущности. Однако это может только помочь в определении похожих слов

**Запишем данные в формате JSON**, чтобы снова не запускать процесс лемматизации

In [85]:
with open('vocab_data/words_to_id.json', 'w', encoding='utf8') as json_file:
    json.dump(words_to_id, json_file)
    
with open('vocab_data/id_to_words.json', 'w', encoding='utf8') as json_file:
    json.dump(id_to_words, json_file)

___________________

Теперь распарсим конкретно словарь гиперонимов

In [12]:
with open('vocab_data/words_to_id.json', encoding='utf8') as json_file:
    words_to_id = json.load(json_file)

In [13]:
with open('vocab_data/id_to_words.json', encoding='utf8') as json_file:
     id_to_words = json.load(json_file)

In [14]:
id_to_words = dict([(int(a), b) for a, b in id_to_words.items()])

In [15]:
with open('RuThes/relations.xml') as xml_file:
    xml = xml_file.read()

In [16]:
root = etree.fromstring(xml)

In [17]:
for relation in root.getchildren():
    lhs = relation.get("from")
    rhs = relation.get("to")
    t = relation.get("name")
    if t == "ВЫШЕ":
        lhs = id_to_words[int(lhs)]
        rhs = id_to_words[int(rhs)] 
        print("[{}; {}]".format(lhs, rhs))

[энергетика; производить товар]
[энергетика; инфраструктурный отрасль]
[электростанция; энергетический объект]
[электростанция; производитель электроэнергия]
[энергия; физический свойство]
[энергетический обеспечение; предоставление услуга]
[электроснабжение; энергетический обеспечение]
[электроснабжение; коммунальный услуга]
[электрический энергия; энергия]
[тепловой энергия; энергия]
[гидроэлектростанция; электростанция]
[линия электропередача; энергетический объект]
[тепловой электростанция; электростанция]
[турбин; энергосиловой установка]
[атомный энергетика; энергетика]
[атомный электростанция; электростанция]
[атомный электростанция; ядерный объект]
[атомный энергия; энергия]
[ядерный реактор; атомный оборудование]
[ядерный реактор; ядерный объект]
[астрономия; естественный наука]
[астрономия; космический исследование]
[наука; сфера деятельность]
[научный работник; служащий]
[доктор наука; научный работник]
[доктор наука; учёный степень]
[кандидат наука; научный работник]
[канди

[хутор; усадьба]
[хранение газ; содержимый в целость]
[газохранилище; помещение для хранение]
[холера; кишечный инфекционный заболевание]
[растительный корма; корм животный]
[зернофураж; растительный корма]
[производственный обучение; профессиональный обучение]
[оросительный система; постройка]
[рецепт врач; документ]
[рентгеновский оборудование; медицинский оборудование]
[телевизионный передача; представление]
[телевизионный передача; телерадиопередача]
[телеграфный агентство; информационный агентство]
[телевизионный станция; оборудование для телевещание]
[телефонный сеть; сеть связь]
[почтовый предприятие; предприятие связь]
[техника безопасность; требование]
[технический наука; прикладной наука]
[тиф; кишечный инфекционный заболевание]
[геологический разведка; разведка]
[гидротехнический строительство; промышленный строительство]
[гидроминеральный ресурс; подземный вод]
[водный перевозка; транспортный перевозка]
[микрохирургия; хирургия]
[грузовой терминал; транспортный терминал]
[г

[декоративно-прикладной искусство; прикладной искусство]
[декоративно-прикладной искусство; пластический искусство]
[промышленный авария; авария]
[железнодорожный авария; транспортный авария]
[ледокольный работа; работа]
[стиральный машина; бытовой электроприбор]
[стиральный машина; потребительский товар длительный пользование]
[термальный источник; подземный вод]
[термальный источник; водный источник]
[верительный грамота; дипломатический документ]
[судоремонтный работа; ремонт]
[акт гражданский состояние; поступок человек]
[семейный положение; статус]
[детский безнадзорность; порок общество]
[неорганический химия; химический наука]
[авиационный компания; транспортный предприятие]
[авиационный отряд; подразделение]
[агроном; сельскохозяйственный работник]
[агроном; земледелец]
[багажник; инструмент]
[бытовой осветительный прибор; бытовой электроприбор]
[бытовой осветительный прибор; осветительный прибор]
[люстра; бытовой осветительный прибор]
[видеоролик; видеопродукция]
[видеоролик; 

[авианосец; надводный судно]
[авианосец; боевой корабль]
[нагревательный прибор; тепловой оборудование]
[автоклав; нагревательный прибор]
[президент государство; глава государство]
[сбор подпись; собрать в один место]
[партия зелёный; политический партия]
[алиби; отсутствие]
[алиби; доказательство по дело]
[антифашистский движение; общественный движение]
[антифашистский движение; стремиться уничтожить]
[агат; халцедон]
[избирательный ящик; ящик]
[мощность взрыв; мощность]
[народный танец; народный творчество]
[народный танец; танец]
[нарушение воинский дисциплина; преступить]
[националист; последователь]
[медресе; духовно-учебный заведение]
[политический борьба; политический деятельность]
[политический борьба; добиваться]
[политический борьба; бороться с соперник]
[резидент; субъект деятельность]
[аминокислота; органический кислота]
[англиканский церковь; протестантизм]
[болезнь кровь; болезнь]
[анемия; болезнь кровь]
[предвыборный кампания; кампания]
[апартеид; расовый сегрегация]
[ап

[хатанга; река]
[латвия; иностранный государство]
[латвия; прибалтийский страна]
[рига; столица государство]
[елгава; город]
[лиепая; город]
[юрмала; город]
[резекне; город]
[сигулда; город]
[екабпилс; город]
[вентспилс; город]
[даугавпилс; город]
[даугава /западный двина/; река]
[озеро; озеро]
[лена; река]
[река; река]
[река; приток река]
[вилюй; река]
[вилюй; приток река]
[согдийский область; область таджикистан]
[худжанд; центр административно-территориальный единица]
[ленинградский область; область рф]
[тосно; город ленинградский область]
[волхов; город ленинградский область]
[выборг; город ленинградский область]
[высоцк; город ленинградский область]
[кириши; город ленинградский область]
[тихвин; город ленинградский область]
[гатчина; город ленинградский область]
[ленинградский область .; город ленинградский область]
[пикалево; город ленинградский область]
[приморск ленинградский область; город ленинградский область]
[ивангород; город ленинградский область]
[кингисепп; город ленинг

...

[заместитель председатель; заместитель руководитель]
[вице-губернатор; государственный служащий]
[вице-губернатор; заместитель должностной лицо]
[вице-спикер; государственный служащий]
[вице-спикер; заместитель председатель]
[подстанция; технический устройство]
[якутянин; житель город]
[славка; певчий птица]
[слезоотделение; выделить из организм]
[двухпалатный парламент; законодательный орган]
[парламентский партия; политический партия]
[партийный собрание; собрание]
[цыганский табор; лагерь]
[съездить туда и обратно; выехать]
[съездить туда и обратно; обернуться туда и обратно]
[слетать туда и обратно; лететь]
[слетать туда и обратно; съездить туда и обратно]
[слизать язык; счистить]
[слизать язык; поднимать )]
[словоизменение; изменение]
[город башкирия; город российский федерация]
[тиражировать; полиграфический работа]
[тиражировать; количество )]
[осмелеть; изменение]
[сумерки; полумрак]
[смести; сбросить вниз]
[смести; сгрести в один место]
[смести; подметать]
[сменный работа; тру

[разрыв; различие]
[разрыв; несоответствие]
[вид ); превратиться]
[вече; собрание]
[омич; житель город]
[прорваться; проявление чувство]
[перерыть в поиск; поиск]
[перерыть в поиск; разобрать )]
[предписать; отдать приказ]
[сочинительный связь; синтаксический связь]
[составиться; начаться]
[подобраться; составиться]
[киль самолёт; плоскость]
[киль самолёт; часть летательный аппарат]
[предсказуемый; допустимый )]
[прикаспийский регион; географический область]
[переработать; сделать заново]
[ухватиться за возможность; употреблять]
[ухватиться за возможность; браться за дело]
[неактуальный; незначительный]
[поглотить; заставить]
[форпост; на который можно опереться )]
[пылать; излучать свет]
[подведомственный; зависимый]
[тоска по прошлый; уныние )]
[натворить; поступок человек]
[натворить; причинение вред]
[незапланированный; неожиданный]
[незапланированный; дополнительный]
[келейный; секретный]
[разнородный смесь; комбинация]
[терзать; вызывать тревога]
[терзать; мучить]
[информированны

[термостойкость; стойкость к воздействие]
[термостойкость; физический свойство]
[устойчивость к высокий температура; термостойкость]
[поступление на работа; поступить]
[экономический класс; пассажирский тариф]
[экономический класс; класс обслуживание]
[сечка; ножевой изделие]
[спортивный плавание; водный вид спорт]
[спортивный плавание; плавание]
[тепловыделение; теплообмен]
[тепловыделение; энергия]
[тепломагистраль; теплопровод]
[тепломагистраль; магистральный линия]
[теплопроводность; проводимость]
[теплопроводность; теплообмен]
[беспроводный связь; телекоммуникационный связь]
[проводной связь; телекоммуникационный связь]
[нелегальный экономика; правонарушение]
[нелегальный экономика; теневой экономика]
[конкурсный торг; торговый операция]
[теплоцентраль; энергетический объект]
[термоядерный энергия; атомный энергия]
[математический теория; математический наука]
[математический теория; научный теория]
[семейство тетеревиный; птица]
[семейство тетеревиный; пернатый дичь]
[производств

[система счисление; формальный система]
[подводный пространство; пространство]
[глубоководный пространство; подводный пространство]
[наезд на пешеход; автомобильный авария]
[наезд на пешеход; сбить вниз]
[наезд на пешеход; наезд транспортный средство]
[столкновение автомобиль; автомобильный авария]
[столкновение автомобиль; столкновение с препятствие]
[наезд транспортный средство; дорожно-транспортный происшествие]
[наезд транспортный средство; столкновение с препятствие]
[наезд транспортный средство; наехать]
[столкнуться с проблема; деятельность]
[исчерпаемый природный ресурс; природный ресурс]
[выброс парниковый газ; загрязнение атмосфера]
[составить целый; войти в состав]
[составить целый; вызвать появление )]
[участок недра; участок]
[жидкий отход; отход]
[жидкий отход; жидкость]
[обращение с отход; работа]
[размещение отход; разместить]
[размещение отход; обращение с отход]
[транспортировка отход; грузовой перевозка]
[транспортировка отход; обращение с отход]
[оценочный деятельно

[силовой упражнение; спортивный тренировка]
[плохой перспектива; перспектива на будущее]
[красный ковровый дорожка; ковровый дорожка]
[суперкар; спортивный автомобиль]
[силовой служба; государственный орган]
[переходник; деталь устройство]
[служебный карьера; повышение в должность]
[служебный карьера; трудовой карьера]
[скупой на проявление чувство; черта характер]
[скупой на проявление чувство; сдержанность в поведение]
[опасность социальный взрыв; угроза]
[комплекс взаимосвязанный часть; целый]
[тусон; город]
[гипсокартон; строительный материал]
[отшельничество; образ жизнь]
[зацикленный на один; устремить )]
[шахтный печь; печь для нагревание]
[трансплантолог; хирург]
[воспользоваться случать; употреблять]
[грамотный с точка зрение язык; соответствовать правило]
[грамотный с точка зрение язык; безошибочный]
[режим реальный время; режим функционирование устройство]
[плакать от радость; проливать слеза]
[нечистый сила; сверхъестественный сущность]
[колёсный база; расстояние]
[косметол

In [18]:
def get_hypernymy_dict(relations_filename):
    hypernyms = defaultdict(list)
    hyponyms = defaultdict(list)
    
    with open(relations_filename) as xml_file:
        xml = xml_file.read()
    root = etree.fromstring(xml)
    
    for relation in root.getchildren():
        lhs = relation.get("from")
        rhs = relation.get("to")
        t = relation.get("name")
        lhs = id_to_words[int(lhs)]
        rhs = id_to_words[int(rhs)]

        if t == "ВЫШЕ":
            hyponyms[rhs].append(lhs)
            hypernyms[lhs].append(rhs)
            
    return hyponyms, hypernyms

In [19]:
hyponyms, hypernyms = get_hypernymy_dict('RuThes/relations.xml')

In [20]:
hypernyms['человек']

['живой организм', 'субъект деятельность']

Видно, что в данном случае всё работает быстро, а значит не обязательно сохранять это в папку со словарями. Таким образом, словарь гиперонимов распарсился и лемматизировался

### Токенизация предложений

Словарь в тезаурусе очень небольшой, поэтому понадобится выделять токены и другие, при этом отдавая приоритет токенам из словаря. Поэтому требуется, чтобы работало распознавание мультитокенов, для этого можно использовать `MWETokenizer` из библиотеки `nltk`

In [21]:
from nltk.tokenize import MWETokenizer, WordPunctTokenizer

In [22]:
def get_tesaurus_multitokens(words_to_id):
    mwes = []
    
    for term in words_to_id.keys():
        splitted = term.split()
        if len(term.split()) > 1:
            mwes.append(tuple(splitted))
    
    return mwes

In [23]:
mwes = get_tesaurus_multitokens(words_to_id)

In [24]:
mwes[:10]

[('v-образный', 'вырез'),
 ('абазинский', 'язык'),
 ('абзац', 'текст'),
 ('абонентский', 'плата'),
 ('абонентский', 'громкоговоритель'),
 ('абонентский', 'обслуживание'),
 ('абразивный', 'материал'),
 ('абразивный', 'работа'),
 ('абрикосовый', 'дерево'),
 ('абрикосовый', 'цвет')]

In [25]:
word_punct_tokenizer = WordPunctTokenizer()
mwe_tokenizer = MWETokenizer(mwes=mwes, separator=' ')

In [26]:
def tokenize_sentence(sentence, need_lemmatize=True):
    if need_lemmatize:
        sentence = lemmatize_sentence(sentence)
    return mwe_tokenizer.tokenize(word_punct_tokenizer.tokenize(sentence))

In [27]:
tokenize_sentence('Саша Исаева - самая лучшая девушка на планете Земля! И улыбается лучше всех')

['саша',
 'исаев',
 '-',
 'самый',
 'хороший',
 'девушка',
 'на',
 'планета земля',
 '!',
 'и',
 'улыбаться',
 'хороший',
 'весь']

### Токенизация из tagged_texts

Задача этого блока в том, чтобы прочитать предложения, которые уже были некоторым образом нормализованы. Дальше соединить в единое целое, а потом разбить на токены так, чтобы там находились слова из тезауруса

In [28]:
def read_sentences_from_tagged_file(filename):
    sentences = []
    with open(filename) as tagged_file:
        current_sentence_tokens = []
        need_append = False
        
        for line in tagged_file.readlines():
            if line.startswith("# sent_id"):
                need_append = True
            elif line.startswith("# text"):
                continue
            elif len(line) < 2:
                sentence_normalized = ' '.join(current_sentence_tokens)
                tokens = tokenize_sentence(sentence_normalized, need_lemmatize=False)
                sentences.append(tokens)
                need_append = False
                current_sentence_tokens = []
            else:
                if need_append:
                    current_sentence_tokens.append(line.split('\t')[2])
    return sentences

In [29]:
np.array(read_sentences_from_tagged_file('Lenta/texts_tagged/20120702strike.txt'))

array([list(['Релиз', 'дополнение', 'Arctic', 'Strike', 'для', 'шутер', 'Ghost', 'Recon', ':', 'Future', 'Soldier', 'отлагать', '.']),
       list(['о', 'это', 'сообщавать', 'портал', 'Videogamer', '.']),
       list(['ранее', 'планировать', ',', 'что', 'оно', 'поступать', 'в', 'продажа', '3', 'июль', '.']),
       list(['Dlс', 'должен', 'быть', 'выходить', 'для', 'Xbox', '360', 'и', 'Ps3', '.', 'издательство', 'Ubisoft', ',', 'который', 'выпускать', 'серия', 'Ghost', 'Recon', ',', 'объяснять', 'перенос', 'то', ',', 'что', 'создатель', 'игра', 'необходимый', 'время', 'на', 'доработка', 'дополнение', '.']),
       list(['по', 'слово', 'он', 'представитель', ',', 'Arctic', 'Strike', 'поступать', 'в', 'продажа', 'до', 'конец', 'июль', '.']),
       list(['точный', 'дата', 'быть', 'объявливать', 'позднебыть', 'дополнение', 'Arctic', 'Strike', 'быть', 'анонсировать', 'в', 'середина', 'май', '.']),
       list(['в', 'он', 'должен', 'воходить', 'несколько', 'карта', 'и', 'новый', 'режим', 'дл

### Разделение на обучение и тест

Разделим в отношении $70$ на $30$ на обучение и тест как словарь гиперонимов, так и набор текстов. Конечная цель - выявление гиперонимов внутри текстов с помощью глубинного обучения, при этом хотим искать те гиперонимы, которые не встречались до этого в словаре (то есть их не видели на обучающей выборке)

Возможно, что в тест стоит брать лишь более поздние тексты, но на самом деле в поисках гиперонимов для пополнения словаря никто не мешает обсматривать и более старые источники информации

In [30]:
text_names = listdir('Lenta/texts_tagged')
train_names, test_names = train_test_split(text_names, test_size=0.3)

In [31]:
len(test_names)

10932

In [32]:
hyponym_keys = list(hyponyms.keys())
train_hyponym_keys, test_hyponym_keys = train_test_split(hyponym_keys, test_size=0.3)

In [33]:
len(test_hyponym_keys)

3271

In [34]:
def make_hyponym_hypernym_dicts(key_subset):
    hypernyms_subset = defaultdict(list)
    hyponyms_subset = defaultdict(list)
    
    for hyper in key_subset:
        for hypo in hyponyms[hyper]:
            hyponyms_subset[hyper].append(hypo)
            hypernyms_subset[hypo].append(hyper)
            
    return hyponyms_subset, hypernyms_subset

In [35]:
train_hyponyms, train_hypernyms = make_hyponym_hypernym_dicts(train_hyponym_keys)

In [36]:
test_hyponyms, test_hypernyms = make_hyponym_hypernym_dicts(test_hyponym_keys)

Найдём, сколько раз встречаются в наборе текстов пары гипонимов и гиперонимов из обучающего и тестового словаря. Для этого научимся вычленять пары гипоним-гипероним из одного предложения.

### Поиск гиперонимов внутри одного предложения

Напишем функцию, которая будет принимать предложения и детектировать в нем гиперонимию, если она есть. Тогда, если она есть, будет отмечать слова, где она встретилась

In [37]:
def find_sentence_hypernymy(sentence, need_tokenization=True):
    if need_tokenization:
        tokens = tokenize_sentence(sentence)
    else:
        tokens = sentence
        
    hyper_ind = None
    hypo_ind = None
    
    n_train = n_test = 0
    marked_sentence = "NOT FOUND"
    
    for i, hypo_cand in enumerate(tokens):
        for j, hyper_cand in enumerate(tokens):
            if hypo_cand in hyponyms[hyper_cand]:
                if len(hypo_cand) > 1 and len(hyper_cand) > 1:
                    if hyper_cand in train_hypernyms:
                        n_train += 1
                    else:
                        n_test += 1
                    hyper_ind = j
                    hypo_ind = i
                    
    if hyper_ind is not None and hyper_ind != hypo_ind:
        sent_tokens = []
        for i, token in enumerate(tokens):
            if i == hypo_ind:
                token = "__" + token + "__"
            elif i == hyper_ind:
                token = "**" + token + "**"
            sent_tokens.append(token)
        marked_sentence = ' '.join(sent_tokens)
        
    return marked_sentence, n_train, n_test

In [38]:
'город' in hyponyms['город']

True

In [39]:
find_sentence_hypernymy('Известно, что приматами являются не только обезьяны, но и люди.')

('известный , что **примат** являться не только __обезьяна__ , но и человек .',
 1,
 0)

Теперь пройдемся по имеющемуся корпусу и попробуем найти подобные предложения в новостях

In [40]:
def get_train_test_hypernyms(filenames, verbose=False):
    n_train_all = 0
    n_test_all = 0
    
    for i, filename in tqdm(enumerate(filenames)):
        sentences_tokens = read_sentences_from_tagged_file(filename)
        
        if verbose and i % 1000 == 0:
            print("{}k: {} {}".format(i // 1000, n_train_all, n_test_all))
        
        for sentence_tokens in sentences_tokens:
            marked, n_train, n_test = find_sentence_hypernymy(sentence_tokens, False)
            n_train_all += n_train
            n_test_all += n_test
    
    return n_train_all, n_test_all

In [90]:
train_paths = [join('Lenta/texts_tagged', filename) for filename in train_names]
test_paths = [join('Lenta/texts_tagged', filename) for filename in test_names]

In [59]:
for i, filename in tqdm(enumerate(train_paths)):
    sentences_tokens = read_sentences_from_tagged_file(filename)
        
    for sentence_tokens in sentences_tokens:
        marked, n_train, n_test = find_sentence_hypernymy(sentence_tokens, False)
        if n_train + n_test > 0:
            print(filename)
            print(marked)
            print()

Lenta/texts_tagged/20160207kadyrov.txt
NOT FOUND

Lenta/texts_tagged/20120905brando.txt
инцидент происходить в время то , как __лидер__ партия Полин Маруа ( Pauline Marois ) произносить со сцена речь , приурочивать к победа на выборы . в результат стрельба один **человек** быть убивать , еще один ранить .

Lenta/texts_tagged/20170108gorka.txt
NOT FOUND

Lenta/texts_tagged/20170108gorka.txt
NOT FOUND

Lenta/texts_tagged/20160606gas.txt
о это в понедельник , 6 июнь , в эфир украинский " 5 канал " заявлять глава " Нафтогаз " андрей Коболев , передавать риа новость . в качество условие он называть согласие " газпром " на внесение временный **изменение** к существуть контракт , который , по он слово , " являться невыгодный и нерыночный " , " с цель приведение цена до уровень , который хоть как - то приближать к рыночный " . материал по теме12 : 26 10 ноябрь 2015Н голуб газуЗач украинский власть отказываться от закупка российский топливо " если цена быть низкий , чем тот цена , который мы пр

Lenta/texts_tagged/20140603blockpos.txt
в свой очередь , в областной управление Мвд взрыв в обладминистрация называть **ошибка** сам ополченец , который якобы , пытаться сбивать самолет из зенитный комплекс , по __оплошность__ выпусчивать ракет по здание .

Lenta/texts_tagged/20121106firstvote.txt
NOT FOUND

Lenta/texts_tagged/20121106firstvote.txt
NOT FOUND

Lenta/texts_tagged/20121106firstvote.txt
NOT FOUND

Lenta/texts_tagged/20100206park.txt
NOT FOUND

Lenta/texts_tagged/20140905redwings.txt
NOT FOUND

Lenta/texts_tagged/20130504karachi.txt
NOT FOUND

Lenta/texts_tagged/20130504karachi.txt
NOT FOUND

Lenta/texts_tagged/20150409airbus320.txt
NOT FOUND

Lenta/texts_tagged/20120706emirates.txt
правительство швейцария приостановлять весь поставка **вооружение** и __военный техника__ объединять арабский Эмирата , сообщать reuters .

Lenta/texts_tagged/20120706emirates.txt
Приостановка военный экспорт и отзывший лицензия у оаэ состояться вскоре после то , как швейцарский газета Sonntagsz

Lenta/texts_tagged/20120502dtp.txt
NOT FOUND

Lenta/texts_tagged/20100902rosavia.txt
в связь с это министр транспорт игорь Левитин 9 август поручать Росавиация и Ростуризй сокращать транзитный пассажиропоток через __московский аэропорт__ . решение министерство ранее уже критиковать ассоциация туроператор россия ( Атор ) , отмечать , что предложение Минтранс перенаправлять транзитный пассажиропоток из столичный аэропорт в регион приводить к рост цена на авиабилет . по мнение Атхор , в случай , если пропускной способность столичный **аэропорт** падать , на московский авиаузел существенно обостряться конкуренция за свободный слот ( время , выделять для выполнение самолет посадка / взлет в определенный дата или период ) .

Lenta/texts_tagged/20130806sharapova.txt
на пятый место оказываться американский автогонщица Даник Патриколо как отмечать forbes , заработка __спортсменка__ по - прежнему сильно уступать доход самый высокооплачиваемый **спортсмен** .

Lenta/texts_tagged/20100607severstal

Lenta/texts_tagged/20100209avalanche.txt
NOT FOUND

Lenta/texts_tagged/20100209avalanche.txt
NOT FOUND

Lenta/texts_tagged/20100209avalanche.txt
NOT FOUND

Lenta/texts_tagged/20100203come.txt
уже тогда астрофизик отмечать необычность объект - внешне он напоминать комета , однако он местоположение ( внутри главный поясо астероид ) вместе с **необычный** траектория заставлять исследователь предполагать , что перед они тело совершенно иной природа . на новый снимок " Хаббвать " хорошо видно , что у основание хвост иметься хаотичный структура , __нехарактерный__ для комета .

Lenta/texts_tagged/20160408poroh.txt
NOT FOUND

Lenta/texts_tagged/20160408poroh.txt
NOT FOUND

Lenta/texts_tagged/20150306sanctions_relieved.txt
Ограничительный мера быть снимать с сын бывший премьер - министр украина николай Азаров -- алексей азарова . Кроме то , санкция решать не продлевать в отношение бывший **руководитель** администрация президент андрей Портнов и ранее занимавать пост __председатель__ служба без

Lenta/texts_tagged/20100507ap.txt
лауреат премия имя герман Гесса ( 1982 ) , __государственный премия__ австрия ( 1986 ) , премия фонд " знамя " ( 1995 ) , **премия** имя жуковский ( 2000 ) .

Lenta/texts_tagged/20170203withoutrusoil.txt
NOT FOUND

Lenta/texts_tagged/20161203nihon.txt
NOT FOUND

Lenta/texts_tagged/20161203nihon.txt
NOT FOUND

Lenta/texts_tagged/20161203nihon.txt
**министр** также подчеркивать , сторона готовый " продолжать линия на максимальный всесторонний развитие отношение во все без исключение сфера " . по слово глава мид , москва рассчитывать , что итог предстоящий визит президент россия владимир путин в япония , а также " готовиться двусторонний документ придавать новый импульс развитие весь комплекс двусторонний отношение " . кроме то , лавров сообщать , что москва " обращать внимание наш японский коллега на тот угроза , который создавать в результат размещение элемент глобальный система противоракетный оборона сша в этот регион " . встреча __министр иностранный

...

Lenta/texts_tagged/20160901apartaments.txt
NOT FOUND

Lenta/texts_tagged/20160901apartaments.txt
NOT FOUND

Lenta/texts_tagged/20160901apartaments.txt
NOT FOUND

Lenta/texts_tagged/20160901apartaments.txt
NOT FOUND

Lenta/texts_tagged/20150707hughjackman.txt
__жена__ голливудский актер Хь Джекман Деборра - вать Фернесс признаваться , что запрещать **супруга** работать с Анджелина джоли .

Lenta/texts_tagged/20150904merkel_approval.txt
NOT FOUND

Lenta/texts_tagged/20150904merkel_approval.txt
NOT FOUND

Lenta/texts_tagged/20151202drugs.txt
соответствующий __документ__ от 30 ноябрь опубликовывать на сайт кабмин в среда , 2 декабрь . " принятый решение направлять на развитие отечественный производство лекарственный препарат " ,-- говорить в **текст** распоряжение . Материала по теме00 : 04 26 октябрь 2015 " мы мало знать о качество " импортозамещенный " лекарство " Онколог сергей Тюляндин о то , почему врач не доверять российский медикаментам00 : 07 19 ноябрь 2015 " мы ждать много разочар

Lenta/texts_tagged/20161209zasedaniesiriya.txt
NOT FOUND

Lenta/texts_tagged/20120308statue.txt
однако после то , как он переизбраться на второй срок ( по официальный данные -- с результат в 97 процент голос ) , быть объявлять , что в страна отныне наступать новый __исторический период__ -- **эпоха** могущество и счастье .

Lenta/texts_tagged/20100208charge.txt
это , к пример , жесткий срок оплата товар , **обязательство** раскрывать условие __договор__ и другой нормы . Антимонопольный служба предлагать вводить предельный размер штраф для торговый сеть в размер миллион рубль .

Lenta/texts_tagged/20141204kto.txt
NOT FOUND

Lenta/texts_tagged/20160105wowzedong.txt
NOT FOUND

Lenta/texts_tagged/20140301sena.txt
NOT FOUND

Lenta/texts_tagged/20151108ethanol.txt
в результат спирт выливаться в **река** __миссисипи__ .

Lenta/texts_tagged/20151108ethanol.txt
NOT FOUND

Lenta/texts_tagged/20151108ethanol.txt
NOT FOUND

Lenta/texts_tagged/20130408hmao.txt
NOT FOUND

Lenta/texts_tagged/20130408

Lenta/texts_tagged/20140606close.txt
NOT FOUND

Lenta/texts_tagged/20140606close.txt
NOT FOUND

Lenta/texts_tagged/20140606close.txt
NOT FOUND

Lenta/texts_tagged/20140606close.txt
NOT FOUND

Lenta/texts_tagged/20140606close.txt
глава __республика__ , выступать в конец июль , сообщать , что задерживать некий " предатель , который служить в спецслужба и который через представитель католической церковь быть связывать с **иностранный государство** " .

Lenta/texts_tagged/20140606close.txt
по слово президент , давать гражданин " давать информация " , кроме то , из - за он __деятельность__ " страдать **человек** , который работать за граница " .

Lenta/texts_tagged/20140202aes.txt
но , по слово замглавный инженер станция валерий шаманский , именно загрузка топливо являться психологический рубеж , после который можно сказать , что " жизнь реактор начинаться " . Белоярский Аэс находиться в **город** Заречный __свердловский область .__

Lenta/texts_tagged/20110209house.txt
NOT FOUND

Lenta/tex

Lenta/texts_tagged/20110407protectandserve.txt
NOT FOUND

Lenta/texts_tagged/20150408bondarchukkamaz.txt
NOT FOUND

Lenta/texts_tagged/20150408bondarchukkamaz.txt
NOT FOUND

Lenta/texts_tagged/20110301dio.txt
лидер Foo Fighters Дэйв Грол , вокалист Judas Priest Роб Хэлфорд и Элис Купер принимать участие в запись альбом в память о покойный __певец__ Роннь Джеймсе Дио , сообщать new Musical express . инициатор выпуск трибьть - диска выступивать вдова **музыкант** Венди Галаксиол ( Wendy Galaxiola ) .

Lenta/texts_tagged/20170203minajj.txt
NOT FOUND

Lenta/texts_tagged/20160909sweden_attack.txt
NOT FOUND




KeyboardInterrupt: 

In [42]:
get_train_test_hypernyms(train_paths, True)

0k: 0 0
1k: 1197 55
2k: 2387 119
3k: 3512 197
4k: 4703 255
5k: 5856 313
6k: 7033 384
7k: 8317 445
8k: 9446 495
9k: 10557 553
10k: 11685 609
11k: 12832 666
12k: 14129 725
13k: 15325 780
14k: 16586 843
15k: 17786 887
16k: 18919 952
17k: 20075 1019
18k: 21283 1088
19k: 22538 1153
20k: 23701 1214
21k: 24901 1265
22k: 26038 1342
23k: 27312 1401
24k: 28504 1463
25k: 29679 1523



(30288, 1555)

In [43]:
get_train_test_hypernyms(test_paths, True)

0k: 0 0
1k: 1136 61
2k: 2357 116
3k: 3510 155
4k: 4713 200
5k: 5938 250
6k: 7110 302
7k: 8341 366
8k: 9581 412
9k: 10742 466
10k: 11895 524



(13001, 572)

Как видим, довольно много вхождений есть, и это ещё при условии, что транзитивное замыкание пока что построено не было

### Автоматический поиск паттернов гиперонимии

В этом разделе построим паттерны, основанные на дереве разбора, предложенные в статье [Snow et al. 2004]

Будем строить дерево разбора, исходя из данных в tagged texts, затем брать пары слов, которые встречаются в предложении гипонимом и гиперонимом, искать кратчайший путь между ними в дереве (можно строить банальный BFS), а затем писать то, что находится на рёбрах этого пути в зависимости от направления прохода по ребру.

При этом вместо существительных, между которыми построено отношение, можно писать {}

**TODO:** Что делать с тем, что токены там не являются токенами в тезаурусе?

**TODO:** Добавить специальные линки и разветвления

Для начала научимся строить дерево разбора

In [67]:
def make_syntax_tree(token_descriptions):
    parents = {}
    children = defaultdict(list)
    root = None
    
    for (i, desc) in enumerate(token_descriptions):
        if desc[-3] == "root":
            root = i
        else:
            parent = int(desc[-4]) - 1
            parents[i] = parent
            children[i].append(parent)
            children[parent].append(i)
            
    return root, parents, children

Следующий шаг - это поиск кратчайшего пути от одного слова до другого. Реализуем всё же через BFS

In [84]:
def find_shortest_path(children, v_from, v_to):
    used = defaultdict(lambda: False)
    prev_in_shortest = {}
    
    q = Queue()
    q.put(v_from)
    
    while not q.empty():
        v = q.get()
        used[v] = True
        
        for u in children[v]:
            if not used[u]:
                q.put(u)
                prev_in_shortest[u] = v
    
    if not used[v_to]:
        return None
    
    path = [v_to]
    curr_vertex = v_to
    
    while curr_vertex != v_from:
        new_vertex = prev_in_shortest[curr_vertex]
        path.append(new_vertex)
        curr_vertex = new_vertex
        
    return path

Теперь, имея информацию о рёбрах и путь, надо научиться записывать эту информацию в виде паттерна. При этом надо не забыть учесть, что гипероним и гипоним надо заменить на какой-нибудь универсальный токен

In [53]:
def make_pattern_from_path(path, token_descriptions, parents):
    hyper_id = path[0]
    hypo_id = path[-1]
    
    pattern = ""
    
    for i in range(len(path) - 1):
        left_id = path[i]
        right_id = path[i + 1]
        
        left_token = token_descriptions[left_id][2]
        right_token = token_descriptions[right_id][2]
        
        if left_id in parents and parents[left_id] == right_id:
            rel = token_descriptions[left_id][-3]
        else:
            rel = token_descriptions[right_id][-3]
            
        left_pos = token_descriptions[left_id][3]
        right_pos = token_descriptions[right_id][3]
        
        if left_id in [hypo_id, hyper_id]:
            left_token = "{}"
        
        if right_id in [hypo_id, hyper_id]:
            right_token = "{}"
            
        new_part = "{}:{}:{}:{}:{}".format(left_token, left_pos, rel, right_pos, right_token)
        pattern += new_part
        pattern += ";"
    
    return pattern[:-1] # Removing last ;

Научимся читать из файла список предложений, где каждое предложение - список token_desctiptions, где каждый token_description - это тоже список из фиксированных в texts tagged полей

In [54]:
def parse_texts_tagged_file(filename):
    sentences = []
    
    with open(filename) as tagged_file:
        current_sentence_tokens = []
        need_append = False
        
        for line in tagged_file.readlines():
            if line.startswith("# sent_id"):
                need_append = True
            elif line.startswith("# text"):
                continue
            elif len(line) < 2:
                sentences.append(current_sentence_tokens)
                need_append = False
                current_sentence_tokens = []
            else:
                if need_append:
                    current_sentence_tokens.append(line.split('\t'))
                    
    return sentences

In [64]:
tokens_description = parse_texts_tagged_file("Lenta/texts_tagged/20100401coverage.txt")[4]

In [65]:
tokens_description

[['1', 'По', 'по', 'ADP', '_', '_', '2', 'case', '_', '_\n'],
 ['2',
  'словам',
  'слово',
  'NOUN',
  '_',
  'Animacy=Inan|Case=Dat|Gender=Neut|Number=Plur',
  '13',
  'parataxis',
  '_',
  '_\n'],
 ['3',
  'Медведева',
  'медведев',
  'PROPN',
  '_',
  'Animacy=Anim|Case=Gen|Gender=Masc|Number=Sing',
  '2',
  'nmod',
  '_',
  'SpaceAfter=No\n'],
 ['4', ',', ',', 'PUNCT', '_', '_', '3', 'punct', '_', '_\n'],
 ['5',
  'подавляющее',
  'подавляющий',
  'ADJ',
  '_',
  'Case=Nom|Degree=Pos|Gender=Neut|Number=Sing',
  '6',
  'amod',
  '_',
  '_\n'],
 ['6',
  'большинство',
  'большинство',
  'NOUN',
  '_',
  'Animacy=Inan|Case=Nom|Gender=Neut|Number=Sing',
  '13',
  'nsubj',
  '_',
  '_\n'],
 ['7',
  'местных',
  'местный',
  'ADJ',
  '_',
  'Case=Gen|Degree=Pos|Number=Plur',
  '8',
  'amod',
  '_',
  '_\n'],
 ['8',
  'жителей',
  'житель',
  'NOUN',
  '_',
  'Animacy=Anim|Case=Gen|Gender=Masc|Number=Plur',
  '6',
  'nmod',
  '_',
  '_\n'],
 ['9', '-', '-', 'PUNCT', '_', '_', '8', 'punct

In [68]:
root, parents, children = make_syntax_tree(tokens_description)

In [69]:
root

12

In [70]:
parents

{0: 1,
 1: 12,
 2: 1,
 3: 2,
 4: 5,
 5: 12,
 6: 7,
 7: 5,
 8: 7,
 9: 12,
 10: 11,
 11: 9,
 13: 12}

In [71]:
children

defaultdict(list,
            {0: [1],
             1: [0, 12, 2],
             12: [1, 5, 9, 13],
             2: [1, 3],
             3: [2],
             4: [5],
             5: [4, 12, 7],
             6: [7],
             7: [6, 5, 8],
             8: [7],
             9: [12, 11],
             10: [11],
             11: [10, 9],
             13: [12]})

In [72]:
path = find_shortest_path(children, 12, 7)

In [73]:
path

[7, 5, 12]

In [74]:
make_pattern_from_path(path, tokens_description, parents)

'{}:NOUN:nmod:NOUN:большинство;большинство:NOUN:nsubj:NOUN:{}'

В этом предложении паттерн выделился верно. Запустим поиск на всех предложениях, которые есть. Пока без особых хитростей.

In [99]:
def find_hypernymy_patterns(filenames):
    patterns_dict = Counter()
    
    for filename in tqdm(filenames):
        sentences_full_info = parse_texts_tagged_file(filename)
        for (num, tokens_description) in enumerate(sentences_full_info):
            tokens = [desc[2] for desc in tokens_description]

            hyper_ind = None
            hypo_ind = None

            n_train = n_test = 0
            marked_sentence = "NOT FOUND"

            for i, hypo_cand in enumerate(tokens):
                for j, hyper_cand in enumerate(tokens):
                    if hypo_cand in hyponyms[hyper_cand]:
                        if len(hypo_cand) > 1 and len(hyper_cand) > 1:
                            if hyper_cand in train_hypernyms:
                                n_train += 1
                            else:
                                n_test += 1
                            hyper_ind = j
                            hypo_ind = i

            if hyper_ind is not None and hyper_ind != hypo_ind:
                root, parents, children = make_syntax_tree(tokens_description)
                path = find_shortest_path(children, hyper_ind, hypo_ind)
                
                if path is None:
                    continue
                
                pattern = make_pattern_from_path(path, tokens_description, parents)
                patterns_dict[pattern] += 1
                
    return patterns_dict

In [100]:
cntr = find_hypernymy_patterns(train_paths)

In [105]:
cntr.most_common(6)

[('{}:NOUN:nmod:NOUN:{}', 281),
 ('{}:NOUN:conj:NOUN:{}', 276),
 ('{}:NOUN:nsubj:VERB:отставать;отставать:VERB:nsubj:NOUN:{}', 83),
 ('{}:PROPN:appos:NOUN:{}', 46),
 ('{}:ADJ:amod:NOUN:{}', 35),
 ('{}:NOUN:appos:NOUN:{}', 35)]